In [2]:
%useLatestDescriptors
%use lets-plot
%use dataframe

# Load data

In [3]:
import org.um.feri.ears.algorithms.gp.GPAlgorithmExecutor
import org.um.feri.ears.util.gp_stats.GPAlgorithmMultiConfigurationsProgressData
import org.um.feri.ears.util.gp_stats.GPProgramSolutionSimple

var dataFile = "C:\\Users\\marko\\UnityProjects\\GenIATraP_refactor\\GeneralTrainingEnvironmentForMAS\\evo_monitor\\src\\data\\multiConfigurationPrograssData.ser"
var progressData = GPAlgorithmMultiConfigurationsProgressData.deserializeState(dataFile)
System.out.println("Progress data loaded from file: " + progressData)

System.out.println("Data size: " +progressData.multiConfigurationProgressData.size)

Progress data loaded from file: org.um.feri.ears.util.gp_stats.GPAlgorithmMultiConfigurationsProgressData@23e6365
Data size: 1


# Prepare helper classes & functions

In [4]:
class SelectedIndividual(
    var selectedConfiguration: Int,
    var selectedRun: Int,
    var selectedGeneration: Int,
    var bestWorstIndividual: Int, // 0 = best, 1 = worst
) {
    constructor() : this(0, 0, 0, 0)
}

In [5]:
import org.um.feri.ears.individual.representations.gp.IndividualMatchResult

fun sumIndividualValues(individualMatchResult: IndividualMatchResult, sumAbsValues: Boolean = false): Double {
    var sum = 0.0
    for (key in individualMatchResult.individualValues.keys) {
        if(sumAbsValues){
            sum += Math.abs(individualMatchResult.individualValues[key]!!)
        }
        else {
            sum += individualMatchResult.individualValues[key]!!
        }
    }

    return sum
}

In [6]:
import org.yaml.snakeyaml.util.Tuple

// Prepare data (best, worst and average individual rating per generation)
fun prepareData(selectedConfiguration: Int, selectedRun: Int, bestGenIndividualsRating: MutableList<GPProgramSolutionSimple>?, worstGenIndividualsRating: MutableList<GPProgramSolutionSimple>?, avgGenIndividualRatings: MutableList<Double>?, bestGenIndividualsRatingAvgFitness: MutableList<Double>?, bestGenIndividualAvgFitnesses: MutableList<GPProgramSolutionSimple>?, worstGenIndividualAvgFitnesses: MutableList<GPProgramSolutionSimple>?, avgGenIndividualAvgFitnesses: MutableList<Double>?){

    var multiConfigurationProgressData = progressData.multiConfigurationProgressData[selectedConfiguration]
    var multiRunProgressData = multiConfigurationProgressData.multiRunProgressData[selectedRun]

    for (genProgressData in multiRunProgressData.gensProgressData) {
        var bestGenIndividualRating = genProgressData.population[0]
        var worstIndividualRating = genProgressData.population[0]
        var avgGenIndividualRating = 0.0

        var bestGenIndividualAvgFitness = genProgressData.population[0]
        var worstIndividualAvgFitness = genProgressData.population[0]
        var avgGenIndividualAvgFitness = 0.0

        for (solution in genProgressData.population) {
            if (solution.finalIndividualFitness.additionalValues["Rating"]!! < bestGenIndividualRating.finalIndividualFitness.additionalValues["Rating"]!!) {
                bestGenIndividualRating = solution
            }

            if (solution.finalIndividualFitness.additionalValues["Rating"]!! > worstIndividualRating.finalIndividualFitness.additionalValues["Rating"]!!) {
                worstIndividualRating = solution
            }

            if(sumIndividualValues(solution.finalIndividualFitness.avgMatchResult) < sumIndividualValues(bestGenIndividualAvgFitness.finalIndividualFitness.avgMatchResult)) {
                bestGenIndividualAvgFitness = solution
            }

            if(sumIndividualValues(solution.finalIndividualFitness.avgMatchResult) > sumIndividualValues(worstIndividualAvgFitness.finalIndividualFitness.avgMatchResult)) {
                worstIndividualAvgFitness = solution
            }

            avgGenIndividualRating += solution.finalIndividualFitness.additionalValues["Rating"]!!
            avgGenIndividualAvgFitness += sumIndividualValues(solution.finalIndividualFitness.avgMatchResult)
        }

        if (bestGenIndividualsRating != null) {
            bestGenIndividualsRating.add(bestGenIndividualRating)
        }
        if (worstGenIndividualsRating != null) {
            worstGenIndividualsRating.add(worstIndividualRating)
        }

        avgGenIndividualRating /= genProgressData.population.size
        if (avgGenIndividualRatings != null) {
            avgGenIndividualRatings.add(avgGenIndividualRating)
        }

        if(bestGenIndividualsRatingAvgFitness != null){
            bestGenIndividualsRatingAvgFitness.add(sumIndividualValues(bestGenIndividualRating.finalIndividualFitness.avgMatchResult))
        }

        if (bestGenIndividualAvgFitnesses != null) {
            bestGenIndividualAvgFitnesses.add(bestGenIndividualAvgFitness)
        }
        if (worstGenIndividualAvgFitnesses != null) {
            worstGenIndividualAvgFitnesses.add(worstIndividualAvgFitness)
        }

        avgGenIndividualAvgFitness /= genProgressData.population.size
        if (avgGenIndividualAvgFitnesses != null) {
            avgGenIndividualAvgFitnesses.add(avgGenIndividualAvgFitness)
        }
    }
}

In [7]:
// TODO Move this to GPProgramSolutionSimple
fun calculateDiversity(solution1: GPProgramSolutionSimple, solution2: GPProgramSolutionSimple, w1: Double, w2: Double) : Double {
    var nodeCountDiversity = 0.0

    // Gather all different node count key
    val nodeCountKeys = mutableSetOf<String>()
    nodeCountKeys.addAll(solution1.nodeCounts.keys)
    nodeCountKeys.addAll(solution2.nodeCounts.keys)

    // Calculate node count diversity
    for (key in nodeCountKeys) {
        val nodeCount1 = solution1.nodeCounts[key] ?: 0
        val nodeCount2 = solution2.nodeCounts[key] ?: 0
        nodeCountDiversity += Math.abs(nodeCount1 - nodeCount2)
    }

    // Normalize node count diversity
    nodeCountDiversity /= (solution1.treeSize + solution2.treeSize)

    // Calculate avg fitness diversity
    var avgFitnessDiversity = 0.0

    // Gather all different avg fitness individual values key
    val avgFitnessKeys = mutableSetOf<String>()
    avgFitnessKeys.addAll(solution1.finalIndividualFitness.avgMatchResult.individualValues.keys)
    avgFitnessKeys.addAll(solution2.finalIndividualFitness.avgMatchResult.individualValues.keys)

    // Calculate avg fitness diversity
    for (key in avgFitnessKeys) {
        val avgFitness1 = solution1.finalIndividualFitness.avgMatchResult.individualValues[key] ?: 0.0
        val avgFitness2 = solution2.finalIndividualFitness.avgMatchResult.individualValues[key] ?: 0.0

        avgFitnessDiversity += Math.abs(avgFitness1 - avgFitness2)
    }

    // Normalize avg fitness diversity
    avgFitnessDiversity /= (Math.abs(sumIndividualValues(solution1.finalIndividualFitness.avgMatchResult, true)) + Math.abs(sumIndividualValues(solution2.finalIndividualFitness.avgMatchResult, true)))

    // Calculate final diversity
    return w1 * avgFitnessDiversity + w2 * nodeCountDiversity
}

# Visualize data (line plot) - Best, worst and average individual rating per generation

In [20]:
// Input params for visualization START
val selectedConfiguration = 0
val selectedRun = 0
// Input params for visualization END

// Prepare data
val bestGenIndividualsRating = mutableListOf<GPProgramSolutionSimple>()
val worstGenIndividualsRating = mutableListOf<GPProgramSolutionSimple>()
val avgGenIndividualRatings = mutableListOf<Double>()
val bestGenIndividualsRatingAvgFitness = mutableListOf<Double>()

val bestGenIndividualAvgFitnesses = mutableListOf<GPProgramSolutionSimple>()
val worstGenIndividualAvgFitnesses = mutableListOf<GPProgramSolutionSimple>()
val avgGenIndividualAvgFitnesses = mutableListOf<Double>()

prepareData(selectedConfiguration, selectedRun, bestGenIndividualsRating, worstGenIndividualsRating, avgGenIndividualRatings, bestGenIndividualsRatingAvgFitness, bestGenIndividualAvgFitnesses, worstGenIndividualAvgFitnesses, avgGenIndividualAvgFitnesses)

var multiConfigurationProgressData = progressData.multiConfigurationProgressData[selectedConfiguration]
var multiRunProgressData = multiConfigurationProgressData.multiRunProgressData[selectedRun]

var lastPhaseName = "";
val generations = mutableListOf<String>()
for (genProgressData in multiRunProgressData.gensProgressData) {
    generations.add(genProgressData.generation.toString() + genProgressData.executionPhaseName.substring(genProgressData.executionPhaseName.length - 6, genProgressData.executionPhaseName.length))
}

// Display data
val dfRating = dataFrameOf(
    "Generation" to generations + generations + generations,
    "Rating" to bestGenIndividualsRating.map { it.finalIndividualFitness.additionalValues["Rating"]!! } + worstGenIndividualsRating.map { it.finalIndividualFitness.additionalValues["Rating"]!! } + avgGenIndividualRatings,
    "Individual" to List(generations.size) { "Best" } + List(generations.size) { "Worst" } + List(generations.size) { "Average" }
)

val dfRatingAvgFitness = dataFrameOf(
    "Generation" to generations,
    "AvgFitness" to bestGenIndividualsRatingAvgFitness,
    "Individual" to List(generations.size) { "Average" }
)

val dfAvgFitness = dataFrameOf(
    "Generation" to generations + generations + generations,
    "AvgFitness" to bestGenIndividualAvgFitnesses.map { sumIndividualValues(it.finalIndividualFitness.avgMatchResult) } + worstGenIndividualAvgFitnesses.map { sumIndividualValues(it.finalIndividualFitness.avgMatchResult) } + avgGenIndividualAvgFitnesses,
    "Individual" to List(generations.size) { "Best" } + List(generations.size) { "Worst" } + List(generations.size) { "Average" }
)

// The plot variable stores a plot with the temperature values for each city
val linePlotRating =
    letsPlot(dfRating.toMap()) { x = "Generation"; y = "Rating"; color = "Individual"} + ggsize(2000,800) + geomPoint(shape = 20) + geomLine() + ggtitle("Best Generation Rating")

val linePlotRatingAvgFitness =
    letsPlot(dfRatingAvgFitness.toMap()) { x = "Generation"; y = "AvgFitness"; color = "Individual"} + ggsize(2000,800) + geomPoint(shape = 20) + geomLine() + ggtitle("Best Generation Rating (Average fitness)")

val linePlotAvgFitness =
    letsPlot(dfAvgFitness.toMap()) { x = "Generation"; y = "AvgFitness"; color = "Individual"} + ggsize(2000,800) + geomPoint(shape = 20) + geomLine() + ggtitle("Best Generation Average fitness")

val plots = listOf(linePlotRating, null, linePlotRatingAvgFitness, null, linePlotAvgFitness, null)
gggrid(plots, ncol=2)

<path d="M0.41882658009164553 98.24910235172442 L0.41882658009164553 98.24910235172442 L2.512959480549873 108.12679651343343 L4.607092381008101 103.1781689929991 L6.7012252814663285 113.86204528337436 L8.795358181924556 105.72757358695458 L10.889491082382783 103.08326111680567 L12.983623982841012 101.55097975353108 L15.077756883299239 97.45662808330994 L17.171889783757468 97.0420559050303 L19.266022684215695 97.0420559050303 L21.360155584673922 105.99005224486925 L23.45428848513215 104.65063810114056 L25.54842138559038 98.9081342868403 L27.642554286048608 106.56303330593066 L29.736687186506835 108.30639322469551 L31.830820086965062 107.6076297376594 L33.92495298742329 111.14279317831036 L36.019085887881516 111.37567935249831 L38.11321878833974 113.84031014014563 L40.20735168879797 113.84031014014563 L42.3014845892562 96.30997869380896 L44.395617489714425 96.9430494161089 L46.48975039017265 115.79578326419913 L48.58388329063088 104.70217815619472 L50.678016191089114 104.94026756922389 L52.77214909154734 95.93148180499772 L54.86628199200557 113.90022486059702 L56.960414892463795 111.30937179585294 L59.05454779292202 106.80444159560784 L61.14868069338025 106.80444159560784 L63.24281359383848 100.79250147837178 L65.3369464942967 104.17337214304766 L67.43107939475493 101.63677071555887 L69.52521229521317 119.63021041199825 L71.61934519567139 108.70325889615951 L73.71347809612962 109.40025548124521 L75.80761099658784 105.51759715842351 L77.90174389704607 107.03948953809436 L79.9958767975043 101.97398657690636 L82.09000969796253 109.75021203020682 L84.18414259842075 108.56860947142941 L86.27827549887898 111.6210313073491 L88.3724083993372 107.68105488518843 L90.46654129979544 105.67718314278751 L92.56067420025366 111.32215496908681 L94.65480710071189 108.09672919042724 L96.74894000117011 111.92894208769162 L98.84307290162835 106.14834866571641 L100.93720580208658 114.77024788080953 L103.0313387025448 112.25421948989187 L105.12547160300304 106.81720727476299 L107.21960450346126 109.76924808700494 L109.31373740391949 106.11902109232454 L111.40787030437771 110.26400562466067 L113.50200320483594 110.29348064814457 L115.59613610529416 106.40983515945241 L117.6902690057524 114.03783578293846 L119.78440190621062 108.08445834378436 L121.87853480666885 120.43934404165945 L123.97266770712707 108.85593971773854 L126.06680060758531 109.93738367755333 L128.1609335080435 112.50710389520735 L130.25506640850173 114.14126827377524 L132.34919930895998 102.32369321045772 L134.4433322094182 109.61725703195818 L136.53746510987642 107.01966124944578 L138.63159801033467 105.25382643783789 L140.7257309107929 109.44425808752648 L142.8198638112511 113.26751401648781 L144.91399671170933 101.65274530858154 L147.00812961216758 110.75597910464629 L149.1022625126258 101.38594311406969 L151.19639541308402 109.01635292211044 L153.29052831354224 101.94471148575063 L155.3846612140005 112.85731785704151 L157.4787941144587 109.33819398741986 L159.57292701491693 106.14469990072689 L161.66705991537515 107.12436830887479 L163.7611928158334 109.87138851517078 L165.85532571629162 105.81012564526566 L167.94945861674984 111.22573010635321 L170.04359151720809 105.89540178154837 L172.1377244176663 109.38802712022208 L174.23185731812453 104.48200018061758 L176.32599021858275 106.746321267802 L178.420123119041 105.27316989059061 L180.51425601949921 102.22861039347714 L182.60838891995743 102.95495454518753 L184.70252182041565 101.97304689496386 L186.7966547208739 104.34181013124244 L188.89078762133212 104.64690686406563 L190.98492052179034 113.74055390499352 L193.07905342224856 107.07241089508553 L195.1731863227068 108.75244224889511 L197.26731922316503 102.79256700907472 L199.36145212362325 112.20355663792765 L201.4555850240815 114.00333246140049 L203.54971792453972 111.52403663748015 L205.64385082499794 106.8778867363697 L207.73798372545616 107.564234425825 L209.8321166259144 106.24833232389186 L211.92624952637263 115.20505321070233 L214.02038242683085 118.12628445116968 L216.114

# Visualize data (radar plot) - Comparison of individuals from different generations, runs & configurations

In [9]:
// Input params for visualization START
val selectedIndividuals = mutableListOf<SelectedIndividual>()
selectedIndividuals.add(SelectedIndividual(0, 0, 100, 0)) // Individual at position
selectedIndividuals.add(SelectedIndividual(0, 0, 132, 0)) // Individual at position

val maxValues = mutableMapOf<String, Double>()
maxValues["SectorExploration"] = 5.0
maxValues["PowerUp_Pickup_Health"] = 10.0
maxValues["PowerUp_Pickup_Ammo"] = 15.0
maxValues["PowerUp_Pickup_Shield"] = 5.0
maxValues["MissilesFired"] = 20.0
maxValues["MissilesFiredAccuracy"] = 50.0
maxValues["SurvivalBonus"] = 5.0
maxValues["OpponentTrackingBonus"] = 5.0
maxValues["OpponentDestroyedBonus"] = 500.0
maxValues["DamageTakenPenalty"] = 50.0
// Input params for visualization END

// Prepare data for visualization
var selectedGPAlgorithmSolutionsSimple = mutableListOf<GPProgramSolutionSimple>()

// Get selected individuals
for (selectedIndividual in selectedIndividuals){
    // Prepare data
    val bestGenIndividualsRating = mutableListOf<GPProgramSolutionSimple>()
    val worstGenIndividualsRating = mutableListOf<GPProgramSolutionSimple>()

    prepareData(selectedIndividual.selectedConfiguration, selectedIndividual.selectedRun, bestGenIndividualsRating, worstGenIndividualsRating, null, null, null, null, null)

    var individual: GPProgramSolutionSimple?;
    if(selectedIndividual.bestWorstIndividual == 0) {
        individual = bestGenIndividualsRating[selectedIndividual.selectedGeneration]
    }
    else {
        individual = worstGenIndividualsRating[selectedIndividual.selectedGeneration]
    }

    selectedGPAlgorithmSolutionsSimple.add(individual!!)
}

// Find all fitness keys
val fitnessKeys = mutableListOf<String>()
for (individual in selectedGPAlgorithmSolutionsSimple) {
    for (key in individual.finalIndividualFitness.avgMatchResult.individualValues.keys) {
        if (key !in fitnessKeys) {
            fitnessKeys.add(key)
        }
    }
}

// Order fitnessKeys
fitnessKeys.sort()

// Build labels for visualization
val labels = mutableListOf<String>()
for (individual in selectedGPAlgorithmSolutionsSimple) {
    labels.addAll(fitnessKeys)
}

val datasets = mutableListOf<MutableList<Double>>()

// Build datasets for visualization
for (individual in selectedGPAlgorithmSolutionsSimple) {
    val dataset = mutableListOf<Double>()
    for (key in fitnessKeys) {
        if(individual.finalIndividualFitness.avgMatchResult.individualValues[key] == null) {
            dataset.add(0.0)
            System.out.println(key + ": 0.0")
            continue
        }
        dataset.add(Math.abs(individual.finalIndividualFitness.avgMatchResult.individualValues[key]!!) / maxValues[key]!!)
        System.out.println(key + ": " + individual.finalIndividualFitness.avgMatchResult.individualValues[key]!!)
    }
    System.out.println("/////////////////////////////")
    datasets.add(dataset)
}

var fitnessKeysIndexed = mutableListOf<Int>()
for (i in 0 until fitnessKeys.size) {
    fitnessKeysIndexed.add(i + 1)
}

var individualValueIdsMapped = mutableListOf<Int>()
var individualMapped = mutableListOf<String>()
var index = 0
for(dataset in datasets) {
    individualValueIdsMapped.addAll(fitnessKeysIndexed)
    individualMapped.addAll(List(fitnessKeys.size) { "Individual " + (index + 1) })
    index++
}

// Build map for visualization
val selectedIndividualsData = mapOf(
    "IndividualValueLabels" to labels,
    "IndividualValueId" to individualValueIdsMapped,
    "Individual" to individualMapped,
    "IndividualValues" to datasets.map { it }.toMutableList().flatten()
)

// Map each fitnessKey to a map 1 -> "fitnessKey1", 2 -> "fitnessKey2", ...
var labelsIndexed = fitnessKeys.mapIndexed { index, s -> index to s }.toMap().mapKeys { it.key + 1 }

letsPlot(selectedIndividualsData) +
        geomArea(flat = true) {   // <-- flat. I.e., do not transform segments to curves
            x = "IndividualValueId"; y = "IndividualValues"
        } +
        geomPoint() { x = "IndividualValueId"; y = "IndividualValues"; color="Individual" } +
        scaleXDiscrete(labels = labelsIndexed) +
        coordPolar()

DamageTakenPenalty: 7.887964
MissilesFired: -2.9727273
MissilesFiredAccuracy: -29.668951
OpponentDestroyedBonus: -208.33331
OpponentTrackingBonus: -1.8779092
PowerUp_Pickup_Ammo: -4.398109
PowerUp_Pickup_Health: -0.3409091
PowerUp_Pickup_Shield: -0.20833635
SectorExploration: -4.4242363
SurvivalBonus: -4.7871823
/////////////////////////////
DamageTakenPenalty: 15.1933155
MissilesFired: -2.2
MissilesFiredAccuracy: -27.125
OpponentDestroyedBonus: -158.33333
OpponentTrackingBonus: -4.4730997
PowerUp_Pickup_Ammo: -3.804165
PowerUp_Pickup_Health: -0.35
PowerUp_Pickup_Shield: -1.6875
SectorExploration: -2.8333352
SurvivalBonus: -4.8170004
/////////////////////////////


<path d="M170.5 97.36886069747322 L177.66810514347642 97.72100712198852 L184.76717751593628 98.77405503296359 L191.7288491696851 100.51786300336107 L198.48607540106048 102.93563720916376 L204.9737804275786 106.00409316307992 L211.1294841032938 109.69367995688464 L216.893903636759 113.9688648528203 L222.21152451671475 118.78847548328528 L227.0311351471797 124.106096363241 L231.30632004311536 129.8705158967062 L234.99590683692008 136.0262195724214 L238.06436279083624 142.51392459893952 L240.48213699663893 149.2711508303149 L242.2259449670364 156.23282248406372 L243.27899287801148 163.33189485652358 L243.63113930252678 170.5 L243.27899287801148 177.66810514347642 L242.2259449670364 184.76717751593628 L240.48213699663893 191.7288491696851 L238.06436279083624 198.48607540106048 L234.99590683692008 204.9737804275786 L231.30632004311536 211.12948410329378 L227.0311351471797 216.893903636759 L222.21152451671475 222.21152451671472 L216.893903636759 227.0311351471797 L211.12948410329378 231.30632004311536 L204.9737804275786 234.99590683692008 L198.48607540106048 238.06436279083624 L191.7288491696851 240.48213699663893 L184.7671775159363 242.2259449670364 L177.66810514347642 243.27899287801148 L170.5 243.63113930252678 L163.33189485652358 243.27899287801148 L156.23282248406372 242.2259449670364 L149.2711508303149 240.48213699663893 L142.51392459893952 238.06436279083624 L136.0262195724214 234.99590683692008 L129.87051589670622 231.3063200431154 L124.106096363241 227.0311351471797 L118.78847548328528 222.21152451671475 L113.96886485282033 216.89390363675903 L109.69367995688462 211.1294841032938 L106.00409316307992 204.97378042757862 L102.93563720916379 198.4860754010605 L100.5178630033611 191.7288491696851 L98.77405503296357 184.7671775159363 L97.72100712198854 177.6681051434764 L97.36886069747322 170.5 L97.72100712198854 163.33189485652363 L98.77405503296357 156.23282248406372 L100.51786300336109 149.2711508303149 L102.93563720916379 142.51392459893952 L106.0040931630799 136.0262195724214 L109.69367995688461 129.87051589670622 L113.9688648528203 124.10609636324097 L118.78847548328525 118.78847548328528 L124.10609636324097 113.96886485282033 L129.8705158967062 109.69367995688464 L136.02621957242138 106.00409316307992 L142.5139245989395 102.93563720916379 L149.27115083031487 100.5178630033611 L156.2328224840637 98.77405503296359 L163.3318948565236 97.72100712198852 L170.5 97.36886069747322 " stroke="rgb(233,233,233)" stroke-opacity="1.0" stroke-width="1.0" fill="none">
 
 <path d="M170.5 24.237721394946448 L184.83621028695285 24.94201424397704 L199.03435503187256 27.048110065927176 L212.9576983393702 30.535726006722143 L226.47215080212095 35.371274418327516 L239.44756085515718 41.50818632615983 L251.7589682065876 48.887359913769274 L263.287807273518 57.437729705640606 L273.9230490334295 67.07695096657056 L283.5622702943594 77.71219272648199 L292.1126400862307 89.24103179341242 L299.49181367384017 101.55243914484282 L305.6287255816725 114.52784919787908 L310.46427399327786 128.0423016606298 L313.9518899340728 141.96564496812744 L316.05798575602296 156.16378971304715 L316.76227860505355 170.5 L316.05798575602296 184.83621028695285 L313.9518899340728 199.03435503187256 L310.46427399327786 212.9576983393702 L305.6287255816725 226.47215080212092 L299.49181367384017 239.44756085515718 L292.1126400862307 251.75896820658755 L283.5622702943594 263.287807273518 L273.9230490334295 273.92304903342944 L263.287807273518 283.5622702943594 L251.75896820658755 292.1126400862307 L239.44756085515718 299.49181367384017 L226.47215080212095 305.6287255816725 L212.9576983393702 310.46427399327786 L199.0343550318726 313.9518899340728 L184.83621028695285 316.05798575602296 L170.5 316.76227860505355 L156.16378971304718 316.05798575602296 L141.9656449681274 313.9518899340728 L128.0423016606298 310.46427399327786 L114.52784919787908 305.6287255816725 L101.55243914484282 299.49181367384017 L89.24103179341246 292.1126400862308 L77.71219272648199 283.5622702943594 L67.0

# Selected Individual Details

In [19]:
import org.jetbrains.letsPlot.intern.Plot

// Input params for visualization START
val selectedIndividuals = mutableListOf<SelectedIndividual>()
selectedIndividuals.add(SelectedIndividual(0, 0, 100, 0)) // Individual at position
selectedIndividuals.add(SelectedIndividual(0, 0, 130, 0)) // Individual at position
// Input params for visualization END

// Prepare data for visualization
var selectedGPAlgorithmSolutionsSimple = mutableListOf<GPProgramSolutionSimple>()

// Get selected individuals
for (selectedIndividual in selectedIndividuals){
    // Prepare data
    val bestGenIndividualsRating = mutableListOf<GPProgramSolutionSimple>()
    val worstGenIndividualsRating = mutableListOf<GPProgramSolutionSimple>()

    prepareData(selectedIndividual.selectedConfiguration, selectedIndividual.selectedRun, bestGenIndividualsRating, worstGenIndividualsRating, null, null, null, null, null)

    var individual: GPProgramSolutionSimple?;
    if(selectedIndividual.bestWorstIndividual == 0) {
        individual = bestGenIndividualAvgFitnesses[selectedIndividual.selectedGeneration]
    }
    else {
        individual = worstGenIndividualAvgFitnesses[selectedIndividual.selectedGeneration]
    }

    selectedGPAlgorithmSolutionsSimple.add(individual!!)
}

var plots = mutableListOf<Plot>()

var index = 0
for (individual in selectedGPAlgorithmSolutionsSimple) {
    var nodeCountsData = mapOf(
        "NodeName" to individual.nodeCounts.keys.toList(),
        "NodeCount" to individual.nodeCounts.values.toList()
    )

    val blankTheme = theme(line=elementBlank(), axis=elementBlank())
    val (w, h) = 800 to 400
    val p = letsPlot(nodeCountsData) + ggsize(w,h) + blankTheme

    val plot = p + geomPie(stat = Stat.identity,
            size = 20, stroke = 1, color = "white", hole = 0.5) { slice = "NodeCount"; fill = "NodeName" } +
            blankTheme +
            scaleFillBrewer(palette = "Set1") + ggtitle("Conf: " + selectedIndividuals[index].selectedConfiguration + " Run: " + selectedIndividuals[index].selectedRun + " Gen: " + selectedIndividuals[index].selectedGeneration + " IndividualID: " + individual.individualId)

    System.out.println(
        "Individual: " + "(Conf: " + selectedIndividuals[index].selectedConfiguration + " Run: " + selectedIndividuals[index].selectedRun + " Gen: " + selectedIndividuals[index].selectedGeneration + " IndividualID: " + individual.individualId + ")\nChangesCount: " + individual.changesCount + "\nFunctionNodesCount: " + individual.functionNodes + "\nTerminalNodesCount: " + individual.terminalNodes + "\nTreeSize: " + individual.treeSize + "\nTreeDepth: " + individual.treeDepth + "\nFitness: " + (individual.finalIndividualFitness.additionalValues["Rating"].toString() + ", " + individual.finalIndividualFitness.additionalValues["StdDeviation"]) + "\nIndividualAvgFitness: " + sumIndividualValues(individual.finalIndividualFitness.avgMatchResult) + "\nIndividualAvgFitnessValues: " + individual.finalIndividualFitness.avgMatchResult.individualValues.map { it.key + ": " + it.value }.toString()
        + "\n\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\"
    )

    index++

    plots.add(plot)
}

gggrid(plots, ncol = 2)

Individual: (Conf: 0 Run: 0 Gen: 100 IndividualID: 11032)
ChangesCount: 63
FunctionNodesCount: 71
TerminalNodesCount: 109
TreeSize: 180
TreeDepth: 11
Fitness: -42.74858, 1.8535446
IndividualAvgFitness: -295.21309139999994
IndividualAvgFitnessValues: [OpponentDestroyedBonus: -265.15152, PowerUp_Pickup_Health: -0.5681818, SectorExploration: -3.606073, SurvivalBonus: -4.541091, DamageTakenPenalty: 14.597287, OpponentTrackingBonus: -3.7276366, PowerUp_Pickup_Ammo: -4.816468, PowerUp_Pickup_Shield: -1.6098454, MissilesFired: -4.3999996, MissilesFiredAccuracy: -21.389563]
\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\\
Individual: (Conf: 0 Run: 0 Gen: 130 IndividualID: 11032)
ChangesCount: 89
FunctionNodesCount: 64
TerminalNodesCount: 101
TreeSize: 165
TreeDepth: 11
Fitness: -33.579227, 1.8518904
IndividualAvgFitness: -275.27657020000004
IndividualAvgFitnessValues: [OpponentDestroyedBonus: -241.0714, PowerUp_Pickup_Health: -1.2121181, SectorExploration: -3.4090912, SurvivalBonus: -4.504772

Conf: 0 Run: 0 Gen: 100 IndividualID: 11032 
 
 
 
 
 
 
 
 
 NodeName 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 Inverter 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 RayHitObject 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 Sequencer 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 ShieldLevelBellow 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 Rotate 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 HealthLevelBellow 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 AmmoLevelBellow 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 MoveForward 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 Shoot 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 Selector 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 Conf: 0 Run: 0 Gen: 130 IndividualID: 11032 
 
 
 
 
 
 
 
 
 NodeName 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 Inverter 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 RayHitObject 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 Sequencer 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 ShieldLevelBellow 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 Rotate 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 HealthLevelBellow 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 AmmoLevelBellow 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 MoveForward 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 Shoot 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 Selector

# Genetic Diversity Graph
Genetic diversity of the population based on the avg fitness and node counts

### Calculation of genetic diversity between 2 individuals
1. Difference in avg fitness -> df
2. Difference in node counts -> dn
3. Normalize both values and multiply by the weights -> diversity = w1 * df_norm +  w2 * dn_norm


In [11]:
// Input params for visualization START
val selectedConfiguration = 0
val selectedRun = 0
val w1 = 0.5
val w2 = 0.5
// Input params for visualization END

val bestGenIndividualsRating = mutableListOf<GPProgramSolutionSimple>()

// Remove first 41 individuals


prepareData(selectedConfiguration, selectedRun, bestGenIndividualsRating, null, null, null, null, null, null)

val gpAlgorithmRunGeneticDiversity = mutableListOf<List<Double?>>()

var diversity = calculateDiversity(bestGenIndividualsRating[82], bestGenIndividualsRating[10], w1, w2)

for(i in 0 until bestGenIndividualsRating.size) {
    var gpAlgorithmGenGeneticDiversity = mutableListOf<Double?>()
    for (j in 0 until bestGenIndividualsRating.size) {
        if(j < i){
            var diversity = calculateDiversity(bestGenIndividualsRating[i], bestGenIndividualsRating[j], w1, w2)
            if(diversity > 1.0 || diversity < 0.0) {
                throw Exception("Diversity out of bounds: " + diversity + ", i: " + i + ", j:" + j)
            }
            gpAlgorithmGenGeneticDiversity.add(diversity)
        }
        else {
            gpAlgorithmGenGeneticDiversity.add(null)
        }
    }
    gpAlgorithmRunGeneticDiversity.add(gpAlgorithmGenGeneticDiversity)
}

var individuals = mutableListOf<Int>()
val generations = mutableListOf<String>()

for (i in 0 until gpAlgorithmRunGeneticDiversity.size) {
    generations.addAll(List(gpAlgorithmRunGeneticDiversity[i].size){(i + 1).toString()})

    for (i in 0 until gpAlgorithmRunGeneticDiversity[i].size) {
        individuals.add(i + 1)
    }
}

val df = dataFrameOf(
    "individuals" to individuals,
    "generations" to generations,
    "diversity" to gpAlgorithmRunGeneticDiversity.flatten()
)

val plot = letsPlot(df.toMap()) { x = "individuals"; y = "generations"; fill = "diversity" } + geomTile() + ggtitle("Genetic Diversity Graph")

plot

# Master Tournament Graph
Tournament between generation best individuals

In [12]:
// Input params for visualization START
val selectedConfiguration = 0
val selectedRun = 0
// Input params for visualization END

val n = 3
val Generation = mutableListOf<Int>()
val Rating = mutableListOf<Double>()

val masterTournamentGraphData = progressData.multiConfigurationProgressData[selectedConfiguration].multiRunProgressData[selectedRun].masterTournamentGraphData;
for (i in 0 until masterTournamentGraphData.size) {
    Generation.addAll(List(n) {i + 1})
    val rating = Math.abs(masterTournamentGraphData[i].finalIndividualFitness.additionalValues["Rating"]!!)
    Rating.addAll(listOf(rating - (2*masterTournamentGraphData[i].finalIndividualFitness.additionalValues["StdDeviation"]!!), rating, rating + (2*masterTournamentGraphData[i].finalIndividualFitness.additionalValues["StdDeviation"]!!)))
}

val data = mapOf<String, Any>(
    "Generation" to Generation,
    "Rating" to Rating
)

letsPlot(data) { x = "Generation"; y = "Rating"}  + geomBoxplot(whiskerWidth = 0.2) + ggtitle("Convergence graph (Tournament between generation best individuals)")

0 
 
 
 
 
 
 
 
 
 20 
 
 
 
 
 
 
 
 
 40 
 
 
 
 
 
 
 
 
 60 
 
 
 
 
 
 
 
 
 80 
 
 
 
 
 
 
 
 
 100 
 
 
 
 
 
 
 
 
 
 
 10 
 
 
 
 
 
 
 20 
 
 
 
 
 
 
 30 
 
 
 
 
 
 
 40 
 
 
 
 
 
 
 50 
 
 
 
 
 
 
 
 
 Convergence graph (Tournament between generation best individuals) 
 
 
 
 
 Rating 
 
 
 
 
 Generation

# Convergence graph
Best individual in the final generation is matched with every best individual from previous generations

In [18]:
// Input params for visualization START
val selectedConfiguration = 0
val selectedRun = 0
// Input params for visualization END

val convergenceGraphData = progressData.multiConfigurationProgressData[selectedConfiguration].multiRunProgressData[selectedRun].convergenceGraphData;

var generations = mutableListOf<String>()
var fitnesses = mutableListOf<Float>()

var lastOpponentMatchIndex: Int = -1;
for (individualMatch in convergenceGraphData.finalIndividualFitness.individualMatchResults){
    // If generations already contains individualMatch.opponentsIDs[0] then just sum fitness
    lastOpponentMatchIndex = generations.indexOf(individualMatch.opponentsIDs[0].toString());

    // Individual already played against this individual -> just sum fitness
    if(lastOpponentMatchIndex > -1){
        fitnesses[lastOpponentMatchIndex] += individualMatch.value;
    }
    else {
        generations.add(individualMatch.opponentsIDs[0].toString())
        fitnesses.add(individualMatch.value)
    }
}

// For each fitness in fitnesses calculate average (/2 because final best individual plays agains each opponent 2 time, once on every side)


// Display data
val df = dataFrameOf(
    "Generation" to generations,
    "Fitness" to fitnesses
)

val plot = letsPlot(df.toMap()) { x = "Generation"; y = "Fitness"} + geomLine() + geomPoint(shape = 20) + ggtitle("Convergence graph")

plot

<path d="M1.0479633031436797 125.61032236016587 L1.0479633031436797 125.61032236016587 L6.287779818862077 125.61032236016587 L11.527596334580476 125.61032236016587 L16.76741285029887 125.47736975053289 L22.00722936601727 243.54605117371187 L27.24704588173567 127.53188809888258 L32.48686239745407 127.53188809888258 L37.72667891317247 37.0753868856844 L42.966495428890866 127.53188809888258 L48.20631194460926 125.50581749257515 L53.446128460327664 37.0753868856844 L58.68594497604606 253.32913689766923 L63.925761491764455 128.31207515475626 L69.16557800748285 37.0753868856844 L74.40539452320125 117.60958816989708 L79.64521103891964 37.0753868856844 L84.88502755463804 127.53188809888258 L90.12484407035645 127.53188809888258 L95.36466058607483 123.5148524048953 L100.60447710179324 41.36200213790215 L105.84429361751164 242.6139431258584 L111.08411013323003 242.6139431258584 L116.32392664894843 161.82841439915916 L121.56374316466683 234.21950146216236 L126.80355968038522 126.78779218313383 L132.04337619610365 127.26986738787105 L137.28319271182204 135.38188984074196 L142.52300922754043 135.38188984074196 L147.76282574325884 40.59891005880853 L153.00264225897723 39.59694729519716 L158.24245877469562 162.53894120626157 L163.48227529041404 27.10259620054318 L168.72209180613243 125.28417827408896 L173.9619083218508 27.10259620054318 L179.20172483756923 27.10259620054318 L184.44154135328762 27.10259620054318 L189.681357869006 117.9026173062529 L194.92117438472442 25.537466102710045 L200.1609909004428 124.39352430686094 L205.4008074161612 27.10259620054318 L210.64062393187962 124.39352430686094 L215.880440447598 124.39352430686094 L221.1202569633164 134.90721646019102 L226.3600734790348 164.58336176574096 L231.5998899947532 160.7897239482058 L236.8397065104716 164.58336176574096 L242.07952302619 255.22655490969993 L247.3193395419084 256.90702023683497 L252.55915605762678 125.14679036771774 L257.79897257334517 124.39352430686094 L263.0387890890636 132.57285891022997 L268.27860560478194 132.57285891022997 L273.51842212050036 217.1547020932367 L278.7582386362188 160.7897239482058 L283.99805515193714 125.71420879858175 L289.23787166765555 125.71420879858175 L294.47768818337397 36.27008701540851 L299.71750469909233 132.57285891022997 L304.95732121481075 41.68060066332442 L310.19713773052916 161.8174855960852 L315.4369542462475 160.7897239482058 L320.67677076196594 117.61652617220221 L325.91658727768436 237.30020639658676 L331.1564037934027 42.290188233547255 L336.39622030912113 137.9331517608194 L341.63603682483955 158.41177680437497 L346.8758533405579 158.41177680437497 L352.1156698562763 121.09609859848142 L357.35548637199474 158.41177680437497 L362.5953028877131 158.41177680437497 L367.8351194034315 121.09609859848142 L373.07493591914994 108.27387314471743 L378.3147524348683 199.46899983277996 L383.5545689505867 199.46899983277996 L388.79438546630513 199.46899983277996 L394.0342019820235 118.1882832702459 L399.2740184977419 118.1882832702459 L404.5138350134603 200.12553970551073 L409.7536515291787 126.10448592267987 L414.9934680448971 36.27008701540851 L420.2332845606155 261.64494142660305 L425.4731010763339 36.1616082572217 L430.7129175920523 14.093553801527014 L435.9527341077707 107.28043431604121 L441.19255062348907 107.26745213484766 L446.4323671392075 287.9628906943904 L451.6721836549259 287.9628906943904 L456.91200017064426 199.46899983277996 L462.1518166863627 237.30020639658676 L467.3916332020811 295.9646298320683 L472.63144971779946 248.40993865602854 L477.8712662335179 112.49685058540162 L483.1110827492363 15.538171741457994 L488.35089926495465 295.9646298320683 L493.59071578067307 27.327724651995766 L498.8305322963915 249.01194080590383 L504.07034881210984 34.24314311946553 L509.31016532782826 155.70540511688503 L514.5499818435467 157.617037336981 L519.7897983592651 226.92172798456014 L525.0296148749835 132.07494612084355 " fill="none" stroke-width="1.6500000000000001" stroke="rgb(71,71,71)" stroke-opacity="1.0">
 
 
 
 
 
 
 
 
 
